# Análisis Exploratorio y Predictivo del Tráfico y Decomiso de Armas Ilícitas en Ecuador (2017–2025)

---

<div align="center">

## Universidad Técnica de Machala
### Facultad de Ingeniería Civil

---

**Asignatura:** Inteligencia de Negocios (7mo Semestre)

**Proyecto:** Análisis de Datos y Modelado Supervisado de Armas Ilícitas

**Grupo:** 4

---

### Integrantes:

| # | Nombre Completo |
|---|-----------------|
| 1 | Azuero Maldonado Ronald Alejandro |
| 2 | Castillo Ortega Brandon Estefano |
| 3 | Peña Paladines Martin Alexander |

---

**Fuente de Datos:** Ministerio del Interior y Policía Nacional del Ecuador

**Período de Análisis:** 2017 - 2025

</div>

# Índice del Proyecto

---

## Estructura del Notebook

| Fase | Título | Descripción |
|------|--------|-------------|
| **0** | Configuración Inicial | Instalación de librerías y preparación del entorno |
| **1** | Visualización Geoespacial | Mapas de calor, puntos y coropléticos de Ecuador |
| **2** | Dashboards Interactivos | Filtros en cascada y exploración de datos |
| **3** | Análisis Descriptivo y KPIs | Tasas, rankings y métricas clave |
| **4** | Modelado Predictivo (ML) | Entrenamiento y comparación de 4 algoritmos |
| **5** | Series de Tiempo | Análisis temporal con ARIMA y Prophet |

---

### Objetivo General

Desarrollar un sistema de análisis exploratorio y predictivo que permita identificar patrones en el tráfico de armas ilícitas en Ecuador, utilizando técnicas de Machine Learning para clasificar el origen de fabricación (Artesanal vs Importada).

### Objetivos Específicos

1. Visualizar geográficamente los puntos de incautación de armas
2. Identificar zonas de alta incidencia (hotspots)
3. Analizar tendencias temporales (2017-2025)
4. Entrenar modelos de clasificación supervisada
5. Evaluar y comparar el rendimiento de múltiples algoritmos
6. Generar predicciones sobre el origen de las armas

# FASE 0:  Configuración Inicial

---

## Librerías Utilizadas

En esta celda instalamos y cargamos todas las dependencias necesarias para el proyecto:

| Librería | Uso |
|----------|-----|
| `pandas` | Manipulación y análisis de datos |
| `numpy` | Operaciones numéricas |
| `plotly` | Visualizaciones interactivas (mapas, gráficos) |
| `ipywidgets` | Controles interactivos (dropdowns, sliders) |
| `scikit-learn` | Algoritmos de Machine Learning |
| `xgboost` | Gradient Boosting optimizado |
| `statsmodels` | Modelos estadísticos (ARIMA) |

---

## Nota Importante

Esta celda debe ejecutarse **primero** antes de cualquier otra celda del notebook para garantizar que todas las librerías estén disponibles.

In [1]:
# ============================================================
# FASE 0: CONFIGURACIÓN INICIAL
# ============================================================

# --- INSTALACIONES ---
! pip install plotly ipywidgets scikit-learn xgboost statsmodels --quiet

# --- HABILITAR WIDGETS EN COLAB ---
from google.colab import output
output.enable_custom_widget_manager()

# --- IMPORTACIONES GENERALES ---
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from ipywidgets import interact, Dropdown
import warnings
warnings.filterwarnings('ignore')

print("Configuración completada exitosamente")
print("=" * 50)
print("Librerías cargadas:")
print("   • pandas, numpy")
print("   • plotly (express, graph_objects)")
print("   • ipywidgets")
print("   • scikit-learn, xgboost, statsmodels")
print("=" * 50)

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 21.8 MB/s eta 0:00:00
Configuración completada exitosamente
Librerías cargadas:
   • pandas, numpy
   • plotly (express, graph_objects)
   • ipywidgets
   • scikit-learn, xgboost, statsmodels


# Carga y Preparación de Datos

---

## Descripción del Dataset

Los datos provienen de fuentes oficiales del **Ministerio del Interior** y la **Policía Nacional del Ecuador**.

### Características del Dataset

| Aspecto | Detalle |
|---------|---------|
| **Período** | 2017 - 2025 |
| **Registros** | Miles de incautaciones documentadas |
| **Formato Original** | Archivos Excel (. xlsx) |
| **Hoja de Datos** | Hoja nombrada `'1'` |

---

## Variables Principales

### Variable Objetivo (Target)
| Variable | Descripción | Valores |
|----------|-------------|---------|
| `fabricacion` | Origen de fabricación del arma | `ARTESANAL`, `IMPORTADA` |

### Variables Predictoras (Features)

| Categoría | Variable | Ejemplo |
|-----------|----------|---------|
| **Temporal** | `fecha_evento` | 2024-01-15 |
| **Temporal** | `hora_evento` | 14:30:00 |
| **Geográfica** | `nombre_provincia` | GUAYAS |
| **Geográfica** | `nombre_canton` | GUAYAQUIL |
| **Coordenadas** | `latitud` | -2.1894 |
| **Coordenadas** | `longitud` | -79.8891 |
| **Descriptiva** | `nombre_objeto` | PISTOLA |
| **Descriptiva** | `tipo_delito` | TENENCIA ILEGAL |

---

## Proceso de Limpieza (ETL)

1. **Extracción:** Lectura de archivos Excel desde la hoja correcta
2. **Transformación:**
   - Conversión de coordenadas (coma → punto decimal)
   - Estandarización de fechas
   - Eliminación de registros nulos
3. **Carga:** Dataset unificado en `df_clean`

---

## Requisito

Antes de continuar, asegúrate de que el DataFrame `df_clean` esté cargado en memoria con los datos limpios.

In [2]:
# ============================================================
# CARGA DE DATOS DESDE EL SISTEMA DE ARCHIVOS DE COLAB
# ============================================================

import pandas as pd
import os

# --- RUTA DE LA CARPETA DONDE ESTÁN LOS ARCHIVOS EN COLAB ---
# Se asume que los archivos .xlsx están directamente en /content/
RUTA_CARPETA = '/content'

print(f"Carpeta de búsqueda de archivos: {RUTA_CARPETA}\n")

# --- LISTAR ARCHIVOS EXCEL ---
archivos = [f for f in os.listdir(RUTA_CARPETA) if f.endswith('.xlsx')]
print("Archivos Excel encontrados:")
if archivos:
    for a in archivos:
        print(f"   • {a}")
else:
    print("   No se encontraron archivos .xlsx en la carpeta especificada.")
    print("   Asegúrese de subir los archivos .xlsx al entorno de Colab.")

# --- CARGAR Y UNIFICAR ---
dataframes = []

for archivo in archivos:
    ruta_completa = os.path.join(RUTA_CARPETA, archivo)
    print(f"\nCargando: {archivo}")
    try:
        df_temp = pd.read_excel(ruta_completa, sheet_name='1')
    except:
        df_temp = pd.read_excel(ruta_completa, sheet_name=0)

    dataframes.append(df_temp)
    print(f"   {len(df_temp):,} registros")

# Si no hay dataframes para concatenar, inicializar df_clean como un DataFrame vacío
if dataframes:
    df_clean = pd.concat(dataframes, ignore_index=True)
else:
    print("\nAdvertencia: No se cargaron archivos Excel. df_clean será un DataFrame vacío.")
    df_clean = pd.DataFrame()

# --- LIMPIAR COORDENADAS Y FILTRAR TARGET ---
if not df_clean.empty:
    for col in ['latitud', 'longitud']:
        if col in df_clean.columns:
            # Convertir a string, reemplazar coma por punto, luego a float
            df_clean[col] = pd.to_numeric(
                df_clean[col].astype(str).str.replace(',', '.', regex=False),
                errors='coerce'
            )

    # --- ELIMINAR NULOS Y DUPLICADOS ---
    if 'fabricacion' in df_clean.columns:
        # Filtrar solo las clases válidas del target
        df_clean = df_clean[df_clean['fabricacion'].isin(['ARTESANAL','IMPORTADA'])]
    else:
        print("Advertencia: La columna 'fabricacion' no se encuentra en el DataFrame.")

    registros_antes = len(df_clean)
    df_clean = df_clean.drop_duplicates()

    # --- RESUMEN ---
    print(f"\n{'='*60}")
    print(f"DATASET UNIFICADO Y FILTRADO EXITOSAMENTE")
    print(f"{'='*60}")
    print(f"Total de registros: {len(df_clean):,}")
    print(f"Duplicados eliminados: {registros_antes - len(df_clean):,}")
    print(f"Total de columnas: {len(df_clean.columns)}")
    print(f"{'='*60}")

    display(df_clean.head(3))
else:
    print(f"\n{'='*60}")
    print(f"DATASET VACÍO. No hay datos para procesar.")
    print(f"{'='*60}")

Carpeta de búsqueda de archivos: /content

Archivos Excel encontrados:
   • mdi_armasilicitas_pm_historico_2017_2024.xlsx
   • mdi_armasilicitas_pm_2025_enero_octubre.xlsx

Cargando: mdi_armasilicitas_pm_historico_2017_2024.xlsx
   59,788 registros

Cargando: mdi_armasilicitas_pm_2025_enero_octubre.xlsx
   9,146 registros

DATASET UNIFICADO Y FILTRADO EXITOSAMENTE
Total de registros: 60,923
Duplicados eliminados: 7,170
Total de columnas: 31


codigo_iccs subtipo_objeto_robado nombre_objeto  cantidad   calibre  \
0  SIN INFORMACION         ARMA DE FUEGO      REVOLVER       1.0  SIN_DATO   
1  SIN INFORMACION         ARMA DE FUEGO      REVOLVER       1.0        22   
2  SIN INFORMACION         ARMA DE FUEGO      REVOLVER       1.0        22   

    clase_arma   calidad_de fabricacion fecha_evento hora_evento  ...  \
0  TIRO A TIRO     DECOMISO   IMPORTADA   2017-01-01    04:50:00  ...   
1  TIRO A TIRO     RETENIDO   ARTESANAL   2017-01-01    03:30:00  ...   
2     SIN_DATO  APREHENDIDO   IMPORTADA   2017-01-01    04:30:00  ...   

  nombre_subcircuito codigo_provincia  nombre_provincia  codigo_canton  \
0       GALO PLAZA 3               12          LOS RÍOS           1205   
1           DAMMER 2               17         PICHINCHA           1701   
2   SALINAS CENTRO 2               24       SANTA ELENA           2403   

  nombre_canton codigo_parroquia nombre_parroquia tipo_delito  \
0       QUEVEDO           120550          QUEVEDO    SIN_DATO   
1         QUITO           170150          KENNEDY    SIN_DATO   
2       SALINAS           240350          SALINAS    SIN_DATO   

                      delito               modalidad  
0  TENENCIA Y PORTE DE ARMAS          NO DETERMINADO  
1   PATRULLAJES Y OPERATIVOS  PATRULLAJE EN VEHICULO  
2  TENENCIA Y PORTE DE ARMAS          NO DETERMINADO  

[3 rows x 31 columns]

In [3]:
# ============================================================
# VERIFICACIÓN DEL DATASET
# ============================================================

# --- VERIFICAR QUE df_clean EXISTE ---
if 'df_clean' not in globals() or df_clean.empty:
    raise ValueError("ERROR: df_clean no existe o está vacío. Carga los datos primero.")

# --- INFORMACIÓN DEL DATASET ---
print("Dataset cargado correctamente")
print("=" * 60)
print(f"Total de registros: {len(df_clean):,}")
print(f"Total de columnas: {len(df_clean.columns)}")
print("=" * 60)

# --- COLUMNAS DISPONIBLES ---
print("\nColumnas principales:")
columnas_clave = ['fabricacion', 'fecha_evento', 'hora_evento',
                  'nombre_provincia', 'nombre_canton', 'latitud',
                  'longitud', 'nombre_objeto', 'tipo_delito']

for col in columnas_clave:
    if col in df_clean.columns:
        print(f"   {col}")
    else:
        print(f"   {col} - NO ENCONTRADA")

# --- MUESTRA DE DATOS ---
print("\nPrimeras 5 filas:")
display(df_clean.head())

# --- DISTRIBUCIÓN DEL TARGET ---
print("\nDistribución de la variable objetivo (fabricacion):")
print(df_clean['fabricacion'].value_counts())

Dataset cargado correctamente
Total de registros: 60,923
Total de columnas: 31

Columnas principales:
   fabricacion
   fecha_evento
   hora_evento
   nombre_provincia
   nombre_canton
   latitud
   longitud
   nombre_objeto
   tipo_delito

Primeras 5 filas:


codigo_iccs subtipo_objeto_robado    nombre_objeto  cantidad   calibre  \
0  SIN INFORMACION         ARMA DE FUEGO         REVOLVER       1.0  SIN_DATO   
1  SIN INFORMACION         ARMA DE FUEGO         REVOLVER       1.0        22   
2  SIN INFORMACION         ARMA DE FUEGO         REVOLVER       1.0        22   
3  SIN INFORMACION        ARMA ARTESANAL  SIN ESPECIFICAR       1.0  SIN_DATO   
4  SIN INFORMACION        ARMA ARTESANAL  SIN ESPECIFICAR       1.0  SIN_DATO   

    clase_arma   calidad_de fabricacion fecha_evento hora_evento  ...  \
0  TIRO A TIRO     DECOMISO   IMPORTADA   2017-01-01    04:50:00  ...   
1  TIRO A TIRO     RETENIDO   ARTESANAL   2017-01-01    03:30:00  ...   
2     SIN_DATO  APREHENDIDO   IMPORTADA   2017-01-01    04:30:00  ...   
3     SIN_DATO   RECUPERADO   ARTESANAL   2017-01-01    05:30:00  ...   
4     SIN_DATO    ENTREGADO   ARTESANAL   2017-01-01    00:15:00  ...   

  nombre_subcircuito codigo_provincia  nombre_provincia  codigo_canton  \
0       GALO PLAZA 3               12          LOS RÍOS           1205   
1           DAMMER 2               17         PICHINCHA           1701   
2   SALINAS CENTRO 2               24       SANTA ELENA           2403   
3   PEDERNALES SUR 1               13            MANABÍ           1317   
4      LOS CEREZOS 1               13            MANABÍ           1301   

  nombre_canton codigo_parroquia nombre_parroquia tipo_delito  \
0       QUEVEDO           120550          QUEVEDO    SIN_DATO   
1         QUITO           170150          KENNEDY    SIN_DATO   
2       SALINAS           240350          SALINAS    SIN_DATO   
3    PEDERNALES           131750       PEDERNALES    SIN_DATO   
4    PORTOVIEJO           130150       PORTOVIEJO    SIN_DATO   

                      delito                       modalidad  
0  TENENCIA Y PORTE DE ARMAS                  NO DETERMINADO  
1   PATRULLAJES Y OPERATIVOS          PATRULLAJE EN VEHICULO  
2  TENENCIA Y PORTE DE ARMAS                  NO DETERMINADO  
3  TENENCIA Y PORTE DE ARMAS                  NO DETERMINADO  
4                      OTROS  AUXILIO A LESIONADOS O HERIDOS  

[5 rows x 31 columns]


Distribución de la variable objetivo (fabricacion):
fabricacion
ARTESANAL    34894
IMPORTADA    26029
Name: count, dtype: int64


# FASE 1: Visualización Geoespacial

---

## Objetivo

Representar visualmente la distribución geográfica de las incautaciones de armas en el territorio ecuatoriano, identificando zonas de alta concentración (hotspots).

---

## Tipos de Visualización

### 1.1 Mapa de Calor (Heatmap)
- **Propósito:** Mostrar densidad de incautaciones
- **Interpretación:** Colores más intensos = Mayor concentración de casos
- **Escala:** Amarillo → Naranja → Rojo (menor a mayor densidad)

### 1.2 Mapa de Puntos/Burbujas
- **Propósito:** Ubicar cada incautación con coordenadas exactas
- **Codificación de Color:**
  - Rojo: Armas Artesanales
  - Azul: Armas Importadas

### 1.3 Mapa Coroplético
- **Propósito:** Comparar provincias por cantidad de incautaciones
- **Interpretación:** Provincias más oscuras = Mayor número de casos

---

## Filtros Disponibles

| Filtro | Opciones |
|--------|----------|
| Origen | TODAS, ARTESANAL, IMPORTADA |
| Año | 2017 - 2025 |
| Provincia | Las 24 provincias del Ecuador |

---

## Preguntas que Responde

- ¿Dónde se concentran las incautaciones?
- ¿Qué provincias tienen más armas artesanales vs importadas?
- ¿Los patrones geográficos cambian según el año?

## 1. 1 Mapa de Calor - Densidad de Incautaciones

---

### Descripción

Este mapa muestra la **densidad** de incautaciones de armas utilizando un gradiente de colores.  Las áreas con mayor concentración de casos aparecen en tonos más cálidos (rojo/naranja).

### Parámetros Técnicos

| Parámetro | Valor | Descripción |
|-----------|-------|-------------|
| `radius` | 15 | Radio de influencia de cada punto |
| `zoom` | 5. 5 | Nivel de acercamiento inicial |
| `center` | -1.83, -78.18 | Centro de Ecuador |
| `color_scale` | YlOrRd | Amarillo → Naranja → Rojo |

### Controles Interactivos

- **Dropdown Origen:** Filtrar por tipo de fabricación
- **Dropdown Año:** Filtrar por período temporal

### Interpretación

- **Zonas Rojas Intensas:** Puntos críticos que requieren mayor atención policial
- **Zonas Amarillas:** Incidencia moderada
- **Zonas Sin Color:** Baja o nula actividad registrada

In [4]:
# ============================================================
# 1.1 MAPA DE CALOR - DENSIDAD DE INCAUTACIONES
# ============================================================

import pandas as pd
import plotly.express as px
from ipywidgets import interact, Dropdown

# --- PREPARAR DATOS ---
df_geo = df_clean.dropna(subset=['latitud', 'longitud']).copy()
df_geo['anio'] = pd.to_datetime(df_geo['fecha_evento']).dt.year

# --- OPCIONES DE FILTROS ---
fabricaciones = ['TODAS'] + df_geo['fabricacion'].dropna().unique().tolist()
años = ['TODOS'] + sorted(df_geo['anio'].dropna().unique().tolist())

# --- FUNCIÓN INTERACTIVA ---
@interact(
    origen=Dropdown(options=fabricaciones, value='TODAS', description='Origen: '),
    anio=Dropdown(options=años, value='TODOS', description='Año: ')
)
def mapa_calor(origen, anio):

    datos = df_geo.copy()
    titulo_extra = ""

    # Filtro por origen
    if origen != 'TODAS':
        datos = datos[datos['fabricacion'] == origen]
        titulo_extra += f" | {origen}"

    # Filtro por año
    if anio != 'TODOS':
        datos = datos[datos['anio'] == anio]
        titulo_extra += f" | {anio}"

    if datos.empty:
        print("Sin datos para estos filtros")
        return

    # Crear mapa de calor
    fig = px.density_mapbox(
        datos,
        lat='latitud',
        lon='longitud',
        radius=15,
        zoom=5.5,
        center={'lat': -1.8312, 'lon': -78.1834},
        mapbox_style='carto-positron',
        title=f"MAPA DE CALOR - INCAUTACIONES DE ARMAS{titulo_extra}",
        color_continuous_scale='YlOrRd'
    )

    fig.update_layout(
        height=600,
        title_x=0.5,
        title_font_size=16
    )

    fig.show()

    # Estadísticas
    print(f"\nTotal de registros mostrados: {len(datos):,}")

interactive(children=(Dropdown(description='Origen: ', options=('TODAS', 'IMPORTADA', 'ARTESANAL'), value='TOD…

## 1.2 Mapa de Puntos - Ubicaciones Exactas

---

### Descripción

Cada punto en el mapa representa una **incautación individual** con su ubicación geográfica exacta (latitud y longitud).

### Codificación de Colores

| Color | Significado |
|-------|-------------|
| 🔴 Rojo | Arma de fabricación **ARTESANAL** |
| 🔵 Azul | Arma de fabricación **IMPORTADA** |

### Información al Pasar el Cursor (Hover)

- Provincia
- Cantón
- Tipo de arma (nombre_objeto)
- Origen de fabricación

### Zoom Dinámico

| Selección | Comportamiento |
|-----------|----------------|
| TODAS las provincias | Vista nacional (zoom = 5.5) |
| Provincia específica | Acercamiento automático (zoom = 8) |

### Uso Práctico

Este mapa permite identificar:
- Rutas de tráfico de armas
- Puntos fronterizos críticos
- Diferencias urbano/rural en tipos de armas

In [5]:
# ============================================================
# 1.2 MAPA DE PUNTOS - UBICACIONES EXACTAS
# ============================================================

import pandas as pd
import plotly.express as px
from ipywidgets import interact, Dropdown

# --- OPCIONES ---
provincias = ['TODAS'] + sorted(df_clean['nombre_provincia'].dropna().unique().tolist())

# --- FUNCIÓN INTERACTIVA ---
@interact(provincia=Dropdown(options=provincias, value='TODAS', description='Provincia: '))
def mapa_puntos(provincia):

    datos = df_clean.dropna(subset=['latitud', 'longitud']).copy()

    # Filtrar por provincia
    if provincia != 'TODAS':
        datos = datos[datos['nombre_provincia'] == provincia]
        zoom = 8
        titulo = provincia
    else:
        zoom = 5.5
        titulo = "ECUADOR"

    if datos.empty:
        print("Sin datos para esta provincia")
        return

    # Colores por fabricación
    colores = {'ARTESANAL': '#e74c3c', 'IMPORTADA': '#3498db'}

    # Crear mapa de puntos
    fig = px.scatter_mapbox(
        datos,
        lat='latitud',
        lon='longitud',
        color='fabricacion',
        hover_data=['nombre_provincia', 'nombre_canton', 'nombre_objeto'],
        zoom=zoom,
        center={'lat': datos['latitud'].mean(), 'lon': datos['longitud'].mean()},
        mapbox_style='carto-positron',
        title=f"MAPA DE PUNTOS - {titulo}",
        color_discrete_map=colores
    )

    fig.update_layout(
        height=600,
        title_x=0.5,
        title_font_size=16
    )

    # Optimizar el tamaño y opacidad de los marcadores para mejorar el rendimiento
    # con un gran número de puntos.
    fig.update_traces(marker=dict(size=3, opacity=0.5))

    fig.show()

    # Estadísticas
    print(f"\nTotal de puntos: {len(datos):,}")
    print(f"Artesanales: {len(datos[datos['fabricacion']=='ARTESANAL']):,}")
    print(f"Importadas: {len(datos[datos['fabricacion']=='IMPORTADA']):,}")

interactive(children=(Dropdown(description='Provincia: ', options=('TODAS', 'AZUAY', 'BOLÍVAR', 'CARCHI', 'CAÑ…

# FASE 2: Dashboards Interactivos (UI/UX)

---

## Objetivo

Proporcionar herramientas de exploración interactiva que permitan al usuario filtrar y analizar los datos según múltiples criterios simultáneos.

---

## Elementos de Interfaz

### Controles Disponibles

| Control | Tipo | Función |
|---------|------|---------|
| Provincia | Dropdown | Filtrar por ubicación geográfica |
| Año Inicio | Dropdown | Límite inferior del rango temporal |
| Año Fin | Dropdown | Límite superior del rango temporal |
| Origen | Dropdown | Filtrar por tipo de fabricación |

### Filtros en Cascada

Los filtros funcionan de manera **acumulativa**:

```
TODOS → Filtro Provincia → Filtro Año → Filtro Origen
         ↓                    ↓            ↓
      Datos                Datos        Datos
      Filtrados           Filtrados    Filtrados
```

---

## Visualizaciones del Dashboard

| Panel | Tipo de Gráfico | Información |
|-------|-----------------|-------------|
| Superior Izq.  | Pie (Dona) | Proporción Artesanal vs Importada |
| Superior Der. | Barras | Tendencia anual de incautaciones |
| Inferior Izq. | Barras Horizontales | Top 10 cantones con más casos |
| Inferior Der. | Barras | Distribución por hora del día |

---

## Casos de Uso

1. **Análisis Provincial:** Seleccionar una provincia específica para ver su comportamiento
2. **Análisis Temporal:** Comparar un año contra otro
3. **Análisis por Origen:** Ver solo armas artesanales o importadas

In [6]:
# ============================================================
# 2.1 DASHBOARD MULTI-FILTRO
# ============================================================

import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from ipywidgets import interact, Dropdown

# --- PREPARAR DATOS ---
df_clean['anio'] = pd.to_datetime(df_clean['fecha_evento']).dt.year

# --- OPCIONES DE FILTROS ---
provincias = ['TODAS'] + sorted(df_clean['nombre_provincia'].dropna().unique().tolist())
años_min = int(df_clean['anio'].min())
años_max = int(df_clean['anio'].max())
fabricaciones = ['TODAS'] + df_clean['fabricacion'].dropna().unique().tolist()

# --- FUNCIÓN INTERACTIVA ---
@interact(
    provincia=Dropdown(options=provincias, value='TODAS', description='Provincia:'),
    anio_inicio=Dropdown(options=list(range(años_min, años_max+1)), value=años_min, description='Desde:'),
    anio_fin=Dropdown(options=list(range(años_min, años_max+1)), value=años_max, description='Hasta:'),
    origen=Dropdown(options=fabricaciones, value='TODAS', description='Origen:')
)
def dashboard_completo(provincia, anio_inicio, anio_fin, origen):

    # Aplicar filtros
    datos = df_clean.copy()
    titulo = "ECUADOR"

    if provincia != 'TODAS':
        datos = datos[datos['nombre_provincia'] == provincia]
        titulo = provincia

    datos = datos[(datos['anio'] >= anio_inicio) & (datos['anio'] <= anio_fin)]

    if origen != 'TODAS':
        datos = datos[datos['fabricacion'] == origen]

    if datos.empty:
        print("Sin datos para estos filtros")
        return

    # Crear subplots 2x2
    fig = make_subplots(
        rows=2, cols=2,
        specs=[[{'type': 'pie'}, {'type': 'bar'}],
               [{'type': 'bar'}, {'type': 'bar'}]],
        subplot_titles=(
            'Origen de Armas',
            'Tendencia Anual',
            'Top 10 Cantones',
            'Incautaciones por Hora'
        )
    )

    # 1. PIE - Origen de armas
    conteo_origen = datos['fabricacion'].value_counts()
    fig.add_trace(
        go.Pie(
            labels=conteo_origen.index,
            values=conteo_origen.values,
            hole=0.4,
            marker_colors=['#e74c3c', '#3498db']
        ),
        row=1, col=1
    )

    # 2. BAR - Tendencia anual
    tendencia = datos.groupby('anio').size().reset_index(name='total')
    fig.add_trace(
        go.Bar(
            x=tendencia['anio'],
            y=tendencia['total'],
            marker_color='#3498db'
        ),
        row=1, col=2
    )

    # 3. BAR - Top 10 cantones
    top_cantones = datos['nombre_canton'].value_counts().head(10)
    fig.add_trace(
        go.Bar(
            x=top_cantones.values,
            y=top_cantones.index,
            orientation='h',
            marker_color='#e74c3c'
        ),
        row=2, col=1
    )

    # 4. BAR - Por hora del día
    datos['hora'] = pd.to_datetime(datos['hora_evento'], format='%H:%M:%S', errors='coerce').dt.hour
    por_hora = datos['hora'].value_counts().sort_index()
    fig.add_trace(
        go.Bar(
            x=por_hora.index,
            y=por_hora.values,
            marker_color='#2ecc71'
        ),
        row=2, col=2
    )

    # Configurar layout
    fig.update_layout(
        height=800,
        title_text=f"DASHBOARD INTEGRAL - {titulo} ({anio_inicio}-{anio_fin})",
        title_x=0.5,
        showlegend=False
    )

    fig.show()

    # KPIs
    print(f"\n{'='*60}")
    print(f"RESUMEN: {len(datos):,} incautaciones")
    print(f"Artesanales: {len(datos[datos['fabricacion']=='ARTESANAL']):,}")
    print(f"Importadas: {len(datos[datos['fabricacion']=='IMPORTADA']):,}")
    print(f"{'='*60}")

interactive(children=(Dropdown(description='Provincia:', options=('TODAS', 'AZUAY', 'BOLÍVAR', 'CARCHI', 'CAÑA…

# FASE 3: Análisis Descriptivo y KPIs

---

## Objetivo

Calcular indicadores clave de rendimiento (KPIs) que permitan medir la magnitud del problema de manera **estandarizada** y comparable.

---

## Tasas Poblacionales

### ¿Por qué usar tasas?

Los números absolutos pueden ser engañosos.  Una provincia con 1,000 incautaciones y 4 millones de habitantes tiene una situación diferente a una con 500 incautaciones y 100,000 habitantes.

### Fórmulas

| Métrica | Fórmula | Uso |
|---------|---------|-----|
| **Tasa por 100,000 hab.** | (Casos / Población) × 100,000 | Estándar internacional |
| **Tasa por 10,000 hab. ** | (Casos / Población) × 10,000 | Ciudades pequeñas |

### Ejemplo Práctico

```
Provincia A: 1,000 casos / 4,000,000 hab = 25 por 100k
Provincia B:  500 casos / 100,000 hab = 500 por 100k

→ Provincia B tiene una tasa 20 veces mayor
```

---

## Rankings y Comparaciones

| Análisis | Descripción |
|----------|-------------|
| Top 10 Cantones | Ciudades con más incautaciones |
| Top 10 por Tasa | Ciudades más peligrosas per cápita |
| Origen por Tipo de Arma | Qué armas son más artesanales o importadas |

---

## Fuente de Datos Poblacionales

Datos del **Instituto Nacional de Estadística y Censos (INEC)** - Proyecciones 2024

In [7]:
# ============================================================
# 3.1 DASHBOARD DE KPIS CON TASAS POBLACIONALES
# ============================================================

import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from ipywidgets import interact, Dropdown

# --- POBLACIÓN POR PROVINCIA (INEC 2024) ---
poblacion_provincias = {
    'GUAYAS': 4387434,
    'PICHINCHA': 3228233,
    'MANABI': 1562079,
    'LOS RIOS': 921763,
    'AZUAY': 881394,
    'EL ORO': 715751,
    'ESMERALDAS': 643654,
    'TUNGURAHUA': 590600,
    'SANTO DOMINGO DE LOS TSACHILAS': 458580,
    'LOJA': 521154,
    'CHIMBORAZO': 524004,
    'IMBABURA': 476257,
    'COTOPAXI': 488716,
    'SANTA ELENA': 401178,
    'SUCUMBIOS': 230503,
    'ORELLANA': 161338,
    'BOLIVAR': 209933,
    'CARCHI': 186869,
    'CAÑAR': 281396,
    'ZAMORA CHINCHIPE': 120416,
    'MORONA SANTIAGO': 196535,
    'NAPO': 133705,
    'PASTAZA': 114202,
    'GALAPAGOS': 33042
}

# --- OPCIONES ---
años = ['TODOS'] + sorted(pd.to_datetime(df_clean['fecha_evento']).dt.year.dropna().unique().tolist())

# --- FUNCIÓN INTERACTIVA ---
@interact(anio=Dropdown(options=años, value='TODOS', description='Año: '))
def kpis_tasas(anio):

    datos = df_clean.copy()
    datos['anio'] = pd.to_datetime(datos['fecha_evento']).dt.year

    if anio != 'TODOS':
        datos = datos[datos['anio'] == anio]

    # Calcular conteo por provincia
    conteo = datos.groupby('nombre_provincia').size().reset_index(name='total')
    conteo['poblacion'] = conteo['nombre_provincia'].map(poblacion_provincias)
    conteo = conteo.dropna(subset=['poblacion'])

    # Calcular tasas
    conteo['tasa_100k'] = (conteo['total'] / conteo['poblacion']) * 100000
    conteo['tasa_10k'] = (conteo['total'] / conteo['poblacion']) * 10000

    # Top 10 por cada métrica
    top_cantidad = conteo.nlargest(10, 'total')
    top_tasa = conteo.nlargest(10, 'tasa_100k')

    # Crear visualización
    fig = make_subplots(
        rows=1, cols=2,
        specs=[[{'type': 'bar'}, {'type': 'bar'}]],
        subplot_titles=('Top 10 - Cantidad Absoluta', 'Top 10 - Tasa por 100,000 hab.')
    )

    # Cantidad absoluta
    fig.add_trace(
        go.Bar(
            x=top_cantidad['total'],
            y=top_cantidad['nombre_provincia'],
            orientation='h',
            marker_color='#3498db',
            text=top_cantidad['total'].astype(int),
            textposition='outside'
        ),
        row=1, col=1
    )

    # Tasa por 100k
    fig.add_trace(
        go.Bar(
            x=top_tasa['tasa_100k'].round(2),
            y=top_tasa['nombre_provincia'],
            orientation='h',
            marker_color='#e74c3c',
            text=top_tasa['tasa_100k'].round(2),
            textposition='outside'
        ),
        row=1, col=2
    )

    fig.update_layout(
        height=500,
        title_text=f"KPIs POR PROVINCIA - {anio if anio != 'TODOS' else 'TODOS LOS AÑOS'}",
        title_x=0.5,
        showlegend=False
    )

    fig.show()

    # Tabla resumen
    print("\nTABLA DE TASAS (Top 10 por tasa):")
    print("=" * 80)
    tabla = top_tasa[['nombre_provincia', 'total', 'poblacion', 'tasa_100k']].copy()
    tabla.columns = ['Provincia', 'Incautaciones', 'Población', 'Tasa x 100k']
    print(tabla.to_string(index=False))

interactive(children=(Dropdown(description='Año: ', options=('TODOS', 2017, 2018, 2019, 2020, 2021, 2022, 2023…

In [8]:
# ============================================================
# 3.2 ANÁLISIS DE ORIGEN DE ARMAS
# ============================================================

import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from ipywidgets import interact, Dropdown

# --- OPCIONES ---
provincias = ['TODAS'] + sorted(df_clean['nombre_provincia'].dropna().unique().tolist())

# --- FUNCIÓN INTERACTIVA ---
@interact(provincia=Dropdown(options=provincias, value='TODAS', description='Provincia:'))
def analisis_origen(provincia):

    datos = df_clean.copy()
    titulo = "NIVEL NACIONAL"

    if provincia != 'TODAS':
        datos = datos[datos['nombre_provincia'] == provincia]
        titulo = provincia

    if datos.empty:
        print("Sin datos")
        return

    # Crear subplots
    fig = make_subplots(
        rows=2, cols=2,
        specs=[[{'type': 'pie'}, {'type': 'bar'}],
               [{'type': 'bar', 'colspan': 2}, None]],
        subplot_titles=(
            'Proporción por Origen',
            'Top 10 Cantones',
            'Origen por Tipo de Arma'
        )
    )

    # 1. Pie de origen
    origen = datos['fabricacion'].value_counts()
    fig.add_trace(
        go.Pie(
            labels=origen.index,
            values=origen.values,
            hole=0.5,
            marker_colors=['#e74c3c', '#3498db']
        ),
        row=1, col=1
    )

    # 2. Top cantones
    top_cantones = datos['nombre_canton'].value_counts().head(10)
    fig.add_trace(
        go.Bar(
            x=top_cantones.values,
            y=top_cantones.index,
            orientation='h',
            marker_color='#e74c3c'
        ),
        row=1, col=2
    )

    # 3. Origen por tipo de arma
    tabla_cruzada = pd.crosstab(datos['nombre_objeto'], datos['fabricacion'])
    tabla_cruzada['total'] = tabla_cruzada.sum(axis=1)
    tabla_cruzada = tabla_cruzada.nlargest(8, 'total')

    for col in ['ARTESANAL', 'IMPORTADA']:
        if col in tabla_cruzada.columns:
            fig.add_trace(
                go.Bar(
                    x=tabla_cruzada.index,
                    y=tabla_cruzada[col],
                    name=col,
                    marker_color='#e74c3c' if col == 'ARTESANAL' else '#3498db'
                ),
                row=2, col=1
            )

    fig.update_layout(
        height=800,
        title_text=f"ANÁLISIS DE ORIGEN - {titulo}",
        title_x=0.5,
        barmode='group'
    )

    fig.show()

    # Resumen
    total = len(datos)
    print(f"\n{'='*60}")
    print(f"RESUMEN DE ORIGEN - {titulo}")
    print(f"{'='*60}")
    for fab, count in origen.items():
        pct = (count/total)*100
        print(f"   {fab}: {count:,} ({pct:.1f}%)")
    print(f"{'='*60}")

interactive(children=(Dropdown(description='Provincia:', options=('TODAS', 'AZUAY', 'BOLÍVAR', 'CARCHI', 'CAÑA…

# FASE 4: Modelado Predictivo (Machine Learning)

---

## Objetivo

Entrenar algoritmos de **Aprendizaje Supervisado** que puedan predecir el origen de fabricación de un arma (Artesanal o Importada) basándose en sus características.

---

## Fundamento Teórico

### ¿Qué es el Aprendizaje Supervisado?

Es un tipo de Machine Learning donde el modelo **aprende de ejemplos etiquetados**:

```
Datos Históricos (con etiquetas conocidas)
            ↓
    Entrenamiento del Modelo
            ↓
    Predicción en Datos Nuevos
```

### ¿Por qué Clasificación?

Nuestro problema es de **clasificación binaria**:
- **Clase 0:** ARTESANAL
- **Clase 1:** IMPORTADA

---

## Algoritmos a Comparar

| # | Algoritmo | Tipo | Características |
|---|-----------|------|-----------------|
| 1 | **Regresión Logística** | Lineal | Simple, interpretable, línea base |
| 2 | **Random Forest** | Ensemble | Robusto, maneja no linealidad |
| 3 | **XGBoost** | Gradient Boosting | Alto rendimiento, ganador de competencias |
| 4 | **Red Neuronal (MLP)** | Deep Learning | Captura patrones complejos |

---

## Variables del Modelo

### Features (X) - Variables de Entrada

| Variable | Tipo | Descripción |
|----------|------|-------------|
| `latitud` | Numérica | Coordenada geográfica |
| `longitud` | Numérica | Coordenada geográfica |
| `provincia_enc` | Categórica | Provincia codificada |
| `canton_enc` | Categórica | Cantón codificado |
| `objeto_enc` | Categórica | Tipo de arma codificado |
| `delito_enc` | Categórica | Tipo de delito codificado |
| `anio` | Numérica | Año del evento |
| `mes` | Numérica | Mes del evento |
| `dia_semana` | Numérica | Día de la semana (0-6) |
| `hora` | Numérica | Hora del día (0-23) |

### Target (y) - Variable a Predecir

| Variable | Valores |
|----------|---------|
| `fabricacion` | 0 = ARTESANAL, 1 = IMPORTADA |

---

## División de Datos

| Conjunto | Porcentaje | Uso |
|----------|------------|-----|
| **Entrenamiento** | 70% | Aprender patrones |
| **Prueba** | 30% | Evaluar rendimiento |

In [9]:
# ============================================================
# 4.1 PREPARACIÓN DE DATOS PARA MACHINE LEARNING
# ============================================================

import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.compose import ColumnTransformer

print("Preparando datos para Machine Learning...")
print("=" * 60)

# --- COPIAR DATOS ---
df_ml = df_clean.copy()

# --- VER DISTRIBUCIÓN DE CLASES ---
print("\nDistribución original de 'fabricacion':")
print(df_ml['fabricacion'].value_counts())

# --- FILTRAR SOLO CLASES VÁLIDAS (ARTESANAL e IMPORTADA) ---
clases_validas = ['ARTESANAL', 'IMPORTADA']
df_ml = df_ml[df_ml['fabricacion'].isin(clases_validas)]

print(f"\nRegistros después de filtrar clases válidas: {len(df_ml):,}")
print(df_ml['fabricacion'].value_counts())

# --- CREAR FEATURES TEMPORALES ---
df_ml['fecha_evento'] = pd.to_datetime(df_ml['fecha_evento'], errors='coerce')
df_ml['anio'] = df_ml['fecha_evento'].dt.year.fillna(2020).astype(int)
df_ml['mes'] = df_ml['fecha_evento'].dt.month.fillna(6).astype(int)
df_ml['dia_semana'] = df_ml['fecha_evento'].dt.dayofweek.fillna(3).astype(int)

# Hora
if 'hora_evento' in df_ml.columns:
    df_ml['hora'] = pd.to_datetime(df_ml['hora_evento'], format='%H:%M:%S', errors='coerce').dt.hour.fillna(12).astype(int)
else:
    df_ml['hora'] = 12

# --- DEFINIR VARIABLES ---
cat_features = ['nombre_provincia','nombre_canton','nombre_objeto','tipo_delito']
num_features = ['anio','mes','dia_semana','hora','latitud','longitud']

X = df_ml[cat_features + num_features]
y = df_ml['fabricacion'].map({'ARTESANAL':0,'IMPORTADA':1})

print(f"\nRegistros para entrenar: {len(X):,}")
print(f"Clases: {y.value_counts()}")

# --- DIVIDIR DATOS ---
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.3, random_state=42, stratify=y
)

# --- TRANSFORMADORES ---
ohe = OneHotEncoder(handle_unknown='infrequent_if_exist', min_frequency=0.01)
scaler = StandardScaler()

preprocess = ColumnTransformer(
    transformers=[
        ('cat', ohe, cat_features),
        ('num', scaler, num_features)
    ],
    remainder='drop'
)

# --- TRANSFORMAR DATOS ---
X_train_transformed = preprocess.fit_transform(X_train)
X_test_transformed = preprocess.transform(X_test)

# --- RESUMEN ---
print("\n" + "=" * 60)
print("DATOS PREPARADOS EXITOSAMENTE")
print("=" * 60)
print(f"Total de registros: {len(df_ml):,}")
print(f"Entrenamiento: {len(X_train):,} ({len(X_train)/len(df_ml)*100:.1f}%)")
print(f"Prueba: {len(X_test):,} ({len(X_test)/len(df_ml)*100:.1f}%)")
print(f"\nFeatures categóricas: {cat_features}")
print(f"Features numéricas: {num_features}")
print("=" * 60)

Preparando datos para Machine Learning...

Distribución original de 'fabricacion':
fabricacion
ARTESANAL    34894
IMPORTADA    26029
Name: count, dtype: int64

Registros después de filtrar clases válidas: 60,923
fabricacion
ARTESANAL    34894
IMPORTADA    26029
Name: count, dtype: int64

Registros para entrenar: 60,923
Clases: fabricacion
0    34894
1    26029
Name: count, dtype: int64

DATOS PREPARADOS EXITOSAMENTE
Total de registros: 60,923
Entrenamiento: 42,646 (70.0%)
Prueba: 18,277 (30.0%)

Features categóricas: ['nombre_provincia', 'nombre_canton', 'nombre_objeto', 'tipo_delito']
Features numéricas: ['anio', 'mes', 'dia_semana', 'hora', 'latitud', 'longitud']


In [ ]:
# ============================================================
# 4.2 ENTRENAMIENTO DE MODELOS DE MACHINE LEARNING (CORREGIDO)
# ============================================================

from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from sklearn.pipeline import Pipeline
from sklearn.model_selection import StratifiedKFold, cross_validate
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.compose import ColumnTransformer
import numpy as np

print("ENTRENANDO MODELOS DE MACHINE LEARNING")
print("=" * 70)

# --- IMPUTADORES ---
cat_imputer = SimpleImputer(strategy='constant', fill_value='DESCONOCIDO')
num_imputer = SimpleImputer(strategy='median')

# --- TRANSFORMADORES ---
ohe = OneHotEncoder(handle_unknown='infrequent_if_exist', min_frequency=0.01)
scaler = StandardScaler()

preprocess = ColumnTransformer(
    transformers=[
        ('cat', Pipeline([('imputer', cat_imputer), ('encoder', ohe)]),
         ['nombre_provincia','nombre_canton','nombre_objeto','tipo_delito']),
        ('num', Pipeline([('imputer', num_imputer), ('scaler', scaler)]),
         ['anio','mes','dia_semana','hora','latitud','longitud'])
    ],
    remainder='drop'
)

# --- DEFINIR MODELOS ---
modelos = {
    '1. Regresión Logística': LogisticRegression(max_iter=2000, random_state=42, class_weight='balanced'),
    '2. Random Forest': RandomForestClassifier(n_estimators=400, random_state=42, n_jobs=-1, class_weight='balanced'),
    '3. XGBoost': XGBClassifier(
        n_estimators=500, random_state=42, eval_metric='logloss', verbosity=0,
        learning_rate=0.05, max_depth=6, subsample=0.8, colsample_bytree=0.8,
        scale_pos_weight=y_train.value_counts()[0]/y_train.value_counts()[1]
    ),
    '4. LightGBM': LGBMClassifier(
        n_estimators=600, random_state=42, learning_rate=0.05,
        subsample=0.8, colsample_bytree=0.8, class_weight='balanced'
    )
}

# --- MÉTRICAS A EVALUAR ---
scoring = {
    'accuracy': 'accuracy',
    'balanced_accuracy': 'balanced_accuracy',
    'f1_macro': 'f1_macro',
    'roc_auc': 'roc_auc'
}

# --- VALIDACIÓN CRUZADA ---
skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
resultados = {}

for nombre, modelo in modelos.items():
    print(f"\nEntrenando {nombre}...")
    pipe = Pipeline([('preprocess', preprocess), ('model', modelo)])

    scores = cross_validate(pipe, X_train, y_train, scoring=scoring, cv=skf, n_jobs=-1)

    resultados[nombre] = {k: np.mean(v) for k, v in scores.items()}

    print(f"   {nombre}")
    for k, v in resultados[nombre].items():
        print(f"      {k}: {v:.4f}")

print("\n" + "=" * 70)
print("RANKING DE MODELOS (por F1_macro):")
print("=" * 70)

ranking = sorted(resultados.items(), key=lambda x: x[1]['test_f1_macro'], reverse=True)
for i, (nombre, data) in enumerate(ranking, 1):
    print(f"   {i}. {nombre}: F1_macro={data['test_f1_macro']:.4f}")

print("=" * 70)

ENTRENANDO MODELOS DE MACHINE LEARNING

Entrenando 1. Regresión Logística...
   1. Regresión Logística
      fit_time: 1.4243
      score_time: 0.2150
      test_accuracy: 0.7641
      test_balanced_accuracy: 0.7477
      test_f1_macro: 0.7519
      test_roc_auc: 0.8304

Entrenando 2. Random Forest...


In [ ]:
# ============================================================
# 4.3 EVALUACIÓN FINAL DE MODELOS EN CONJUNTO DE PRUEBA
# ============================================================

from sklearn.metrics import classification_report, confusion_matrix, roc_auc_score, roc_curve
import matplotlib.pyplot as plt
import seaborn as sns

print("EVALUACIÓN FINAL DE MODELOS")
print("=" * 70)

# --- Evaluar cada modelo en X_test ---
for nombre, modelo in modelos.items():
    print(f"\nEvaluando {nombre}...")

    # Pipeline con preprocesamiento
    pipe = Pipeline([('preprocess', preprocess), ('model', modelo)])
    pipe.fit(X_train, y_train)

    # Predicciones
    y_pred = pipe.predict(X_test)
    y_proba = pipe.predict_proba(X_test)[:,1] if hasattr(pipe[-1], 'predict_proba') else None

    # Reporte de clasificación
    print("\nClassification Report:")
    print(classification_report(y_test, y_pred, target_names=['ARTESANAL','IMPORTADA']))

    # Matriz de confusión
    cm = confusion_matrix(y_test, y_pred)
    plt.figure(figsize=(5,4))
    sns.heatmap(cm, annot=True, fmt='d', cmap='Blues',
                xticklabels=['ARTESANAL','IMPORTADA'],
                yticklabels=['ARTESANAL','IMPORTADA'])
    plt.title(f"Matriz de Confusión - {nombre}")
    plt.ylabel('Real')
    plt.xlabel('Predicho')
    plt.show()

    # Curva ROC
    if y_proba is not None:
        auc = roc_auc_score(y_test, y_proba)
        fpr, tpr, _ = roc_curve(y_test, y_proba)
        plt.figure(figsize=(6,5))
        plt.plot(fpr, tpr, label=f'{nombre} (AUC={auc:.3f})')
        plt.plot([0,1],[0,1],'--', color='gray')
        plt.xlabel('False Positive Rate')
        plt.ylabel('True Positive Rate')
        plt.title(f"Curva ROC - {nombre}")
        plt.legend()
        plt.show()

In [ ]:
# ============================================================
# 4.4 SELECCIÓN Y GUARDADO DEL MEJOR MODELO
# ============================================================

import joblib

print("SELECCIÓN DEL MEJOR MODELO")
print("=" * 70)

# --- Seleccionar el mejor modelo según F1_macro ---
ranking = sorted(resultados.items(), key=lambda x: x[1]['test_f1_macro'], reverse=True)
mejor_nombre, mejor_scores = ranking[0]
mejor_modelo = modelos[mejor_nombre]

print(f"Mejor modelo: {mejor_nombre}")
print("Métricas promedio en validación cruzada:")
for k,v in mejor_scores.items():
    print(f"   {k}: {v:.4f}")

# --- Entrenar el mejor modelo en todo el conjunto de entrenamiento ---
final_pipe = Pipeline([('preprocess', preprocess), ('model', mejor_modelo)])
final_pipe.fit(X_train, y_train)

# --- Evaluar en conjunto de prueba ---
y_pred_final = final_pipe.predict(X_test)
y_proba_final = final_pipe.predict_proba(X_test)[:,1]

print("\nClassification Report (Test):")
print(classification_report(y_test, y_pred_final, target_names=['ARTESANAL','IMPORTADA']))

print("\nConfusion Matrix (Test):")
print(confusion_matrix(y_test, y_pred_final))

print(f"\nROC-AUC (Test): {roc_auc_score(y_test, y_proba_final):.4f}")

# --- Guardar el pipeline completo ---
joblib.dump(final_pipe, 'modelo_fabricacion_armas.pkl')
print("\nModelo guardado como 'modelo_fabricacion_armas.pkl'")

In [ ]:
# ============================================================
# 4.5 PREDICCIÓN CON NUEVOS DATOS
# ============================================================

import joblib
import pandas as pd

# --- Cargar el modelo entrenado ---
modelo_final = joblib.load('modelo_fabricacion_armas.pkl')

# --- Ejemplo de nuevos datos (simulación) ---
nuevos_datos = pd.DataFrame({
    'nombre_provincia': ['GUAYAS', 'PICHINCHA'],
    'nombre_canton': ['GUAYAQUIL', 'QUITO'],
    'nombre_objeto': ['PISTOLA', 'REVOLVER'],
    'tipo_delito': ['TENENCIA ILEGAL', 'PORTE ILEGAL'],
    'anio': [2025, 2025],
    'mes': [12, 12],
    'dia_semana': [2, 4],
    'hora': [14, 22],
    'latitud': [-2.1894, -0.2295],
    'longitud': [-79.8891, -78.5249]
})

# --- Predicciones ---
predicciones = modelo_final.predict(nuevos_datos)
probabilidades = modelo_final.predict_proba(nuevos_datos)

# --- Mostrar resultados ---
for i, fila in nuevos_datos.iterrows():
    print(f"\nRegistro {i+1}:")
    print(f"Provincia: {fila['nombre_provincia']} | Cantón: {fila['nombre_canton']} | Objeto: {fila['nombre_objeto']}")
    print(f"Predicción: {'ARTESANAL' if predicciones[i]==0 else 'IMPORTADA'}")
    print(f"Probabilidad Artesanal: {probabilidades[i][0]:.3f} | Probabilidad Importada: {probabilidades[i][1]:.3f}")

# FASE 5:  Análisis de Series de Tiempo

---

## Objetivo

Analizar la **evolución temporal** de las incautaciones y generar **predicciones futuras** sobre la tendencia.

---

## Fundamento Teórico

### ¿Qué es una Serie de Tiempo?

Una secuencia de observaciones ordenadas cronológicamente:

```
Ene-2017 → Feb-2017 → Mar-2017 → ...  → Dic-2025
   50         63         45              78
```

### Componentes de una Serie

| Componente | Descripción | Ejemplo |
|------------|-------------|---------|
| **Tendencia** | Dirección general | Crecimiento sostenido |
| **Estacionalidad** | Patrones repetitivos | Más incautaciones en diciembre |
| **Ruido** | Variaciones aleatorias | Fluctuaciones impredecibles |

---

## Modelos Implementados

### ARIMA (AutoRegressive Integrated Moving Average)

```
AR(p): Autoregresivo - usa valores pasados
I(d): Integrado - diferenciación para estacionariedad
MA(q): Media Móvil - usa errores pasados
```

**Configuración:** ARIMA(2, 1, 2)

---

## Métricas de Evaluación

| Métrica | Fórmula | Interpretación |
|---------|---------|----------------|
| **RMSE** | √(Σ(real-pred)²/n) | Error cuadrático medio |
| **MAE** | Σ\|real-pred\|/n | Error absoluto promedio |

**Menor valor = Mejor modelo**

In [ ]:
# ============================================================
# 5.1 ANÁLISIS DE TENDENCIA TEMPORAL (CORREGIDO)
# ============================================================

import pandas as pd
import plotly.graph_objects as go
from ipywidgets import interact, Dropdown

# --- PREPARAR SERIE TEMPORAL ---
df_tiempo = df_clean.copy()
df_tiempo['fecha'] = pd.to_datetime(df_tiempo['fecha_evento'], errors='coerce')
df_tiempo = df_tiempo.dropna(subset=['fecha'])

# Agrupar por mes y rellenar meses faltantes con 0
serie_mensual = df_tiempo.groupby(pd.Grouper(key='fecha', freq='M')).size()
serie_mensual = serie_mensual.resample('M').sum().fillna(0).reset_index()
serie_mensual.columns = ['fecha','total']

# --- OPCIONES ---
fabricaciones = ['TODAS'] + df_clean['fabricacion'].dropna().unique().tolist()

# --- FUNCIÓN INTERACTIVA ---
@interact(origen=Dropdown(options=fabricaciones, value='TODAS', description='Origen:'))
def serie_tiempo(origen):

    datos = df_tiempo.copy()
    if origen != 'TODAS':
        datos = datos[datos['fabricacion'] == origen]

    serie = datos.groupby(pd.Grouper(key='fecha', freq='M')).size()
    serie = serie.resample('M').sum().fillna(0).reset_index()
    serie.columns = ['fecha','total']

    # Medias móviles
    serie['media_movil_3m'] = serie['total'].rolling(window=3).mean()
    serie['media_movil_6m'] = serie['total'].rolling(window=6).mean()

    # Gráfico
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=serie['fecha'], y=serie['total'],
                             mode='lines+markers', name='Datos Reales',
                             line=dict(color='#3498db')))
    fig.add_trace(go.Scatter(x=serie['fecha'], y=serie['media_movil_3m'],
                             mode='lines', name='Media Móvil 3M',
                             line=dict(color='#e74c3c', dash='dash')))
    fig.add_trace(go.Scatter(x=serie['fecha'], y=serie['media_movil_6m'],
                             mode='lines', name='Media Móvil 6M',
                             line=dict(color='#2ecc71', width=2)))

    fig.update_layout(height=500,
                      title=f"SERIE TEMPORAL DE INCAUTACIONES - {origen if origen!='TODAS' else 'TODOS'}",
                      title_x=0.5, xaxis_title='Fecha', yaxis_title='Cantidad',
                      hovermode='x unified')
    fig.show()

    # Estadísticas
    print(f"\nEstadísticas de la serie:")
    print(f"   • Promedio mensual: {serie['total'].mean():.1f}")
    print(f"   • Máximo: {serie['total'].max()} ({serie.loc[serie['total'].idxmax(),'fecha'].strftime('%Y-%m')})")
    print(f"   • Mínimo: {serie['total'].min()} ({serie.loc[serie['total'].idxmin(),'fecha'].strftime('%Y-%m')})")

In [ ]:
# ============================================================
# 5.2 MODELO ARIMA - PREDICCIÓN TEMPORAL (CORREGIDO)
# ============================================================

import pandas as pd
import numpy as np
import plotly.graph_objects as go
from statsmodels.tsa.arima.model import ARIMA
from sklearn.metrics import mean_squared_error, mean_absolute_error
import warnings
warnings.filterwarnings('ignore')

# --- PREPARAR SERIE ---
df_tiempo = df_clean.copy()
df_tiempo['fecha'] = pd.to_datetime(df_tiempo['fecha_evento'], errors='coerce')
df_tiempo = df_tiempo.dropna(subset=['fecha'])

# Serie mensual con conteo de incautaciones
serie = df_tiempo.groupby(pd.Grouper(key='fecha', freq='M')).size()
serie = serie.resample('M').sum().fillna(0)

# --- DIVIDIR DATOS ---
train = serie[:-6]
test = serie[-6:]

print("Entrenando modelo ARIMA(2,1,2)...")

# --- ENTRENAR MODELO ---
modelo_arima = ARIMA(train, order=(2,1,2))
modelo_fit = modelo_arima.fit()

# --- PREDICCIONES ---
predicciones_test = modelo_fit.forecast(steps=6)
predicciones_futuro = modelo_fit.forecast(steps=12)

# Fechas futuras
fechas_futuro = pd.date_range(start=serie.index[-1] + pd.DateOffset(months=1),
                              periods=12, freq='M')

print("Modelo entrenado exitosamente")

# --- VISUALIZACIÓN ---
fig = go.Figure()
fig.add_trace(go.Scatter(x=serie.index, y=serie.values,
                         mode='lines+markers', name='Datos Reales',
                         line=dict(color='#3498db')))
fig.add_trace(go.Scatter(x=test.index, y=predicciones_test,
                         mode='lines+markers', name='Predicción (Test)',
                         line=dict(color='#e74c3c', dash='dash')))
fig.add_trace(go.Scatter(x=fechas_futuro, y=predicciones_futuro,
                         mode='lines+markers', name='Predicción Futura',
                         line=dict(color='#2ecc71', dash='dot')))

fig.update_layout(height=500, title="MODELO ARIMA - PREDICCIÓN DE INCAUTACIONES",
                  title_x=0.5, xaxis_title='Fecha', yaxis_title='Incautaciones',
                  hovermode='x unified')
fig.show()

# --- MÉTRICAS ---
rmse = np.sqrt(mean_squared_error(test, predicciones_test))
mae = mean_absolute_error(test, predicciones_test)

print(f"\nMÉTRICAS DEL MODELO ARIMA:")
print(f"   RMSE: {rmse:.2f}")
print(f"   MAE: {mae:.2f}")

print(f"\nPREDICCIÓN PRÓXIMOS 6 MESES:")
for fecha, pred in zip(fechas_futuro[:6], predicciones_futuro[:6]):
    print(f"   {fecha.strftime('%Y-%m')}: {int(pred)} incautaciones")

In [ ]:
# ============================================================
# 5.3 MODELO PROPHET - PREDICCIÓN TEMPORAL
# ============================================================

import pandas as pd
import plotly.graph_objects as go
from prophet import Prophet
from sklearn.metrics import mean_squared_error, mean_absolute_error

# --- PREPARAR SERIE ---
df_tiempo = df_clean.copy()
df_tiempo['fecha'] = pd.to_datetime(df_tiempo['fecha_evento'], errors='coerce')
df_tiempo = df_tiempo.dropna(subset=['fecha'])

# Serie mensual con conteo de incautaciones
serie = df_tiempo.groupby(pd.Grouper(key='fecha', freq='M')).size().reset_index(name='y')
serie.rename(columns={'fecha':'ds'}, inplace=True)

# --- DIVIDIR DATOS ---
train = serie.iloc[:-6]
test = serie.iloc[-6:]

# --- ENTRENAR MODELO PROPHET ---
modelo_prophet = Prophet(yearly_seasonality=True, weekly_seasonality=False, daily_seasonality=False)
modelo_prophet.fit(train)

# --- PREDICCIONES ---
futuro = modelo_prophet.make_future_dataframe(periods=12, freq='M')
forecast = modelo_prophet.predict(futuro)

# --- VISUALIZACIÓN ---
fig = go.Figure()

# Datos reales
fig.add_trace(go.Scatter(x=serie['ds'], y=serie['y'],
                         mode='lines+markers', name='Datos Reales',
                         line=dict(color='#3498db')))

# Predicciones en test
pred_test = forecast.set_index('ds').loc[test['ds'], 'yhat']
fig.add_trace(go.Scatter(x=test['ds'], y=pred_test,
                         mode='lines+markers', name='Predicción (Test)',
                         line=dict(color='#e74c3c', dash='dash')))

# Predicciones futuras
pred_futuro = forecast.set_index('ds').loc[futuro['ds'][-12:], 'yhat']
fig.add_trace(go.Scatter(x=pred_futuro.index, y=pred_futuro.values,
                         mode='lines+markers', name='Predicción Futura',
                         line=dict(color='#2ecc71', dash='dot')))

fig.update_layout(height=500, title="MODELO PROPHET - PREDICCIÓN DE INCAUTACIONES",
                  title_x=0.5, xaxis_title='Fecha', yaxis_title='Incautaciones',
                  hovermode='x unified')
fig.show()

# --- MÉTRICAS ---
mse = mean_squared_error(test['y'], pred_test)   # devuelve MSE
rmse = np.sqrt(mse)                              # calculamos RMSE manualmente
mae = mean_absolute_error(test['y'], pred_test)

print(f"\nMÉTRICAS DEL MODELO PROPHET:")
print(f"   RMSE: {rmse:.2f}")
print(f"   MAE: {mae:.2f}")

print(f"\nPREDICCIÓN PRÓXIMOS 6 MESES:")
for fecha, pred in zip(pred_futuro.index[:6], pred_futuro.values[:6]):
    print(f"   {fecha.strftime('%Y-%m')}: {int(pred)} incautaciones")